In [2]:
# sélectionner un numéro d'infolettre (>0)
num = await input("Entrez un numéro d\'infolettre")

Entrez un numéro d'infolettre 1


In [3]:
# modules
%pip install markdown
from bs4 import BeautifulSoup
import pandas as pd
import datetime
import markdown

In [4]:
df_infolettre = pd.DataFrame(await grist.fetch_selected_table())
df_infolettre = df_infolettre.set_index('Numero')

In [5]:
numero = int(num)
# contenu de l'infolettre
contenu_preredige = df_infolettre.loc[numero, 'Contenu_preredige']
titre_principal_txt = df_infolettre.loc[numero, 'Titre_principal']
resume_txt = df_infolettre.loc[numero, 'Resume']
articles = df_infolettre.loc[numero, 'Articles_a_partager']

In [6]:
# modele de base de l'infolettre en html
df_modele_html = pd.DataFrame(await grist.fetch_table('Modele_Infolettre_SIG'))
html_base = df_modele_html.at[0, 'html_base']

In [7]:
# transformation pour beautifulsoup
soup = BeautifulSoup(html_base)

In [8]:
# modification du contenu général
titre_principal = soup.find(id="main-title")
titre_principal.string = titre_principal_txt
resume = soup.find(id="resume")
resume.string = resume_txt

In [13]:
# modification pour chaque article                
df_articles = pd.DataFrame(await grist.fetch_table('Contenu_infolettre'))
df_articles = df_articles.set_index('id_article')
n = 1
for id_art in articles:
    art = df_articles.loc[id_art]
    ids_to_update = {'titre-$': [],
                     'soustitre-$': [],
                     'themes-$': [],
                     'date-$': [],
                    'description-$': [],
                    'miniature-$': [],
                    'savoirplus-$': []}
    titre = art['Titre_article']
    ids_to_update['titre-$'].append(titre)
    soustitre = art['Sous_titre']
    ids_to_update['soustitre-$'].append(soustitre)
    date = art['Date']
    ids_to_update['date-$'].append(date)
    themes = art['Themes_cles']
    ids_to_update['themes-$'].append(themes)
    description = art['Description']
    ids_to_update['description-$'].append(description)
    miniature = art['Miniature']
    ids_to_update['miniature-$'].append(miniature)
    lien = art['Lien']
    ids_to_update['savoirplus-$'].append(lien)
    ids = {key.replace('$', str(n)): value for key, value in ids_to_update.items()}
    for id_html, values in ids.items():
        content = values[0]
        if id_html.startswith(("titre","soustitre")):
            text_html = soup.find(id=id_html)
            text_html.string = content
        elif id_html.startswith("description"):
            text_html = soup.find(id=id_html)
            markdown_as_html = markdown.markdown(content)
            markdown_as_soup = BeautifulSoup(markdown_as_html, 'html.parser')
            # Vider le contenu existant
            text_html.clear()
            for elem in markdown_as_soup.contents:
                text_html.append(elem)
        elif isinstance(content, list):
            content_txt = ", ".join(content)
            text_html = soup.find(id=id_html)
            text_html.string = content_txt
        elif id_html.startswith('date'):
            timestamp = datetime.datetime.fromtimestamp(content)
            date_txt = timestamp.strftime('%d/%m/%Y')
            text_html = soup.find(id=id_html)
            text_html.string = date_txt
        elif id_html.startswith('miniature'):
            img = soup.find(id=id_html)
            img["src"] = miniature
        elif id_html.startswith('savoirplus'):
            ensavoirplus = soup.find(id=id_html)
            print(ensavoirplus)
            ensavoirplus["href"] = lien
    n += 1

<a href="" id="savoirplus-1">Pour en savoir plus</a>


In [15]:
# copier/coller dans le champ Contenu prérédigé et dans un fichier html
soup.prettify()

<!DOCTYPE html>
<html lang="fr-FR" xmlns:o="urn:schemas-microsoft-com:office:office" xmlns:v="urn:schemas-microsoft-com:vml">
 <head>
  <title>
  </title>
  <meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
  <meta content="width=device-width, initial-scale=1.0" name="viewport"/>
  <!--[if mso]>
<xml><w:WordDocument xmlns:w="urn:schemas-microsoft-com:office:word"><w:DontUseAdvancedTypographyReadingMail/></w:WordDocument>
<o:OfficeDocumentSettings><o:PixelsPerInch>96</o:PixelsPerInch><o:AllowPNG/></o:OfficeDocumentSettings></xml>
<![endif]-->
  <!--[if !mso]><!-->
  <link href="https://fonts.googleapis.com/css2?family=Lato:wght@100;200;300;400;500;600;700;800;900" rel="stylesheet" type="text/css"/>
  <link href="https://fonts.googleapis.com/css2?family=Montserrat:wght@100;200;300;400;500;600;700;800;900" rel="stylesheet" type="text/css"/>
  <!--<![endif]-->
  <style>
   * {
			box-sizing: border-box;
		}

		body {
			margin: 0;
			padding: 0;
		}

		a[x-apple-data-det